# Coursera Spacecraft Dynamics and Control - Kinematics
## Module 4
## Concept Check 1 - Saturated Control

In [2]:
import numpy as np
from plotly import graph_objects as pgo
from plotly import express as px
import scipy
import pandas as pd
import sys

sys.path.append('../../')

import attitude_math as am

### Setup
Generic Differential Kinematic function for questions 4 and 5

In [3]:
def f(state, t, H_dot, I_inv):
    sigma = state[:3]
    omega = state[3:]

    sigma_dot = am.MRP_omega_DKE(sigma, omega)
    # Note in the below H_dot omega_R/N is zero and
    # the omega cross I*omega is cancelled
    omega_dot = I_inv @ H_dot
    state_dot = np.concatenate([sigma_dot, omega_dot])
    return state_dot

def Full_State_MRP_short_integrator(pdot,p0,t0,tf,dt):
    """
    Integrate quaternion rates to get new attitude quaternion
    """
    length=int((tf-t0)/dt)+1
    p=np.zeros([length,6])
    p[0,:]=np.array([p0])
    for i,t in enumerate(np.arange(t0, tf, dt)):
        p_new = p[i] + pdot(p[i],t).transpose()*dt
        p[i+1,:] = p_new
        p[i+1,:3] = am.MRP_short(p_new[:3])
    return p

Consider the tracking problem where the unperturbed spacecraft is driven to the reference orientation defined through 

$\sigma_{R/N}=(0.2\sin(ft),0.3\cos(ft),−0.3\sin(ft))$ 

with $f=0.05$. The initial states are 

$\sigma_{B/N}(t_0) = (0.1, 0.2, -0.1)$ 

and 

$\omega_{B/N}(t_0) = (30, 10, -20)$ deg/sec.

Use the globally asymptotically stabilizing control solution 

$u=-K\sigma_{B/R}-[P]\omega_{B/R}+I+[{\omega}_{B/N}][I]\omega_{B/N}-L$

Use the gains 
$K = 5$ Nm and 
$P = 10$ Nms where 
$[P]=P[I_{3\times3}]$. Assume the external torque 
$L$ is zero here. The principal inertias are 
$I_1 = 100 kg m^2$ , 
$I_2 = 75 kg m^2$ , and 
$I_3 = 80 kg m^2$ . Assume the control torque is saturated at 
$u_{\text{max}} = 1$ Nm. Simulate numerically the expected closed-loop response for 3 minutes where you use the unsaturated response if 
$|u|<u_{\text{max}}$ and the saturated response elsewhere. What is the tracking error MRP norm $|\sigma_{B/R}|$ at 60 seconds into the simulation?

In [15]:
I = np.diag([100,75,80])
I_inv = np.linalg.inv(I)
K = 5
P = 10 * np.eye(3)
sigma_0 = np.array([0.1, 0.2, -0.1])
omega_0 = np.deg2rad(np.array([30,10,-20]))
state_0 = np.concatenate([sigma_0,omega_0])
freq = 0.05
control_sat = 1

# Reference Tracking State Functions
sigma_r = lambda t, f :  [0.2*np.sin(f*t), 0.3*np.cos(f*t), -0.3*np.sin(f*t)]
sigma_dot_r = lambda t, f : [0.2*f*np.cos(f*t), -0.3*f*np.sin(f*t), -0.3*f*np.cos(f*t)]
def state_r(t, dt, f) : 
    sigma = sigma_r(t, f)
    sigma_dot = sigma_dot_r(t, f)
    sigma_old = sigma_r(t-dt, f)
    sigma_dot_old = sigma_dot_r(t-dt, f)

    omega_r = am.MRPdot_2_omega(sigma, sigma_dot)
    omega_r_old = am.MRPdot_2_omega(sigma_old, sigma_dot_old)

    omega_r_dot = (omega_r-omega_r_old)/dt
    return np.concatenate([sigma, omega_r, omega_r_dot])

# H_dot with regulator cancellations for speed up
def H_dot(state, state_r, I, K, P):
    sigma = state[:3]
    omega = state[3:]

    att_diff = am.DCM_2_MRP(am.MRP_2_DCM(sigma)@am.MRP_2_DCM(state_r[:3]).transpose())
    omega_r_br = am.MRP_2_DCM(att_diff)@state_r[3:6]
    omega_rdot_br = am.MRP_2_DCM(att_diff)@state_r[6:]
    tracking_term = omega_rdot_br - np.cross(omega, omega_r_br)
    # Note the w X IW terms no longer cancel W saturation
    control = - K*att_diff - P@(omega-omega_r_br) + I @ tracking_term + np.cross(omega, I@omega)
    control = np.minimum(np.maximum(control,-control_sat),control_sat)
    # Note the L cancels from the contol so it ignored
    return  control - np.cross(omega, I@omega)

# Integrate the MRP differential kinematic equations
t_step = .01
t_f = 3*60

dot = lambda state, t : f(state, t, H_dot(state, state_r(t, t_step, freq), I, K, P), I_inv)
#state_t = scipy.integrate.odeint(dot, state_0, np.arange(0., t_f, t_step))
state_t = Full_State_MRP_short_integrator(dot, state_0, 0., t_f, t_step)

# Calculate the MRP norm squared
time_measure=60
answer_i  = int(time_measure/t_step)
del_sigma = am.DCM_2_MRP(am.MRP_2_DCM(state_t[answer_i,:3])@am.MRP_2_DCM(sigma_r(time_measure, freq)).transpose())
print(f"At Time: {time_measure}\tMRP B/R: {del_sigma}\tand its Norm: {np.linalg.norm(del_sigma)}")

# Plots
fig = pgo.Figure()
sigma = np.array([sigma_r(t,freq) for t in np.arange(0., t_f, t_step)])
sigma_dot = np.array([sigma_dot_r(t,freq) for t in np.arange(0., t_f, t_step)])
fig.add_scatter3d(x=state_t[:,0], y=state_t[:,1], z=state_t[:,2],mode="lines")
fig.add_scatter3d(x=sigma[:,0],y=sigma[:,1],z=sigma[:,2],mode="lines")
fig.show()

state_data = np.concatenate([np.array(np.arange(0., t_f+t_step, t_step)).reshape(-1,1),state_t],axis=1)
state_data = pd.DataFrame(state_data, columns=["t","sigma1","sigma2","sigma3","omega1","omega2","omega3"])
px.line(state_data,x="t",y=state_data.columns[1:4]).show()

px.line(state_data,x="t",y=state_data.columns[4:]).show()

At Time: 60	MRP B/R: [ 0.31519073 -0.29287323  0.29281668]	and its Norm: 0.5204435950564774
